# Difference

The `git diff` command allows you to chech difference between condition of repository.

## Untracked files

Untracked files wont be displayed in `git diff`.

The following example just init git repository and add a file there and the `git diff` command doesn't print anything in this case.

In [2]:
%%bash
mkdir diff_example
cd diff_example

git init &> /dev/null
echo "some text" > test_file
git diff

cd ..
rm -r diff_example

## Changed files

By default `git diff` shows unstaged changes. In fact, any change to the file can be described as an insert/delete. So the following subsections show what it's like to have insert/delete lines in the `git diff` results.

### Insert line

Main point of the next cell is to add line `"second line"` to the file commited before. In `git diff` results it'll look like `+second line`.

In [5]:
%%bash
mkdir diff_example
cd diff_example

git init &> /dev/null
echo "first line" > test_file
git add test_file &> /dev/null
git commit -m "initial commit" &> /dev/null


echo "second line" >> test_file
git diff

cd ..
rm -r diff_example

diff --git a/test_file b/test_file
index 08fe272..06fcdd7 100644
--- a/test_file
+++ b/test_file
@@ -1 +1,2 @@
 first line
+second line


### Delete line

In this case I created files with two lines `"first line"` and `"second line"`. After committing, I save the new version of the file without the `second line`. Gid diff shows it as `-second line`.

In [12]:
%%bash
mkdir diff_example
cd diff_example
git init &> /dev/null

cat > test_file << EOF
first line
second line
EOF
git add test_file
git commit -m "initial commit" &> /dev/null

cat > test_file << EOF
first line
EOF
git diff

cd ..
rm -r diff_example

diff --git a/test_file b/test_file
index 06fcdd7..08fe272 100644
--- a/test_file
+++ b/test_file
@@ -1,2 +1 @@
 first line
-second line


## New file

In this section, I'll show you what a newly added file looks like in git diff.

### Empty file

In the following example, I've added an empty `second_file` and compared it with the state of the repository in the previous commit, if there is no `second_file' line, the `new file mode` will signal that this file has been created.

In [20]:
%%bash
mkdir diff_example
cd diff_example
git init &> /dev/null

touch first_file
git add first_file
git commit -m "first commit" &> /dev/null

touch second_file
git add second_file &> /dev/null

git diff --staged
cat second_file

cd ..
rm -r diff_example

diff --git a/second_file b/second_file
new file mode 100644
index 0000000..e69de29


### File with content

In this example I have created a file `second_file` and added some content to it. It'll share all the details of adding empty file option - `new file mode 100644` signal that new file has been created. But there is also a section with changes to the file below. Note that the source file from the commit to which we are comparing the state is marked as `--- /dev/null` (in Linux this directory is used for information that should simply be deleted).

In [21]:
%%bash
mkdir diff_example
cd diff_example
git init &> /dev/null

touch first_file
git add first_file
git commit -m "first commit" &> /dev/null

echo "some content" > second_file
git add second_file &> /dev/null

git diff --staged
cat second_file

cd ..
rm -r diff_example

diff --git a/second_file b/second_file
new file mode 100644
index 0000000..2ef267e
--- /dev/null
+++ b/second_file
@@ -0,0 +1 @@
+some content
some content


## --staged option

By default `git diff` shows only changed but not staged files. To get information about staged files use `--staged` option.

### New file

By using the `--staged` option, you can even see the difference between a newly created (but added) file.

So in the following example I have created and added to the repo file and compared the results with and without the `--staged` option.

In [11]:
%%bash
mkdir diff_example
cd diff_example

git init &> /dev/null
echo "some text" > staged_file
git add staged_file

echo "=====just diff===="
git diff

echo
echo "=====diff staged====="
git diff --staged

cd ..
rm -r diff_example

=====just diff====

=====diff staged=====
diff --git a/staged_file b/staged_file
new file mode 100644
index 0000000..7b57bd2
--- /dev/null
+++ b/staged_file
@@ -0,0 +1 @@
+some text


### Unstaged changes

If you use the `--staged` option, you won't see any difference when unstaging files. In the example:

- In the first commit I just added `first_file`;
- I added `second_file` and staged it;
- I changed `first_file` but did not stage it;
- Using `git diff' without the `--staged' option I only got changes in `first_file` because it wasn't staged;
- Using `git diff --staged` I only got information about `second_file` but not about `first_file`.

In [14]:
%%bash
mkdir diff_example
cd diff_example
git init &> /dev/null

echo "first text" > first_file
git add first_file
git commit -m "first file add" &> /dev/null

echo "sefond text" > second_file
git add second_file
echo "changed first text" > first_file

echo "=====just diff===="
git diff

echo
echo "=====diff staged====="
git diff --staged

cd ..
rm -r diff_example

=====just diff====
diff --git a/first_file b/first_file
index 38181e5..fc9cf92 100644
--- a/first_file
+++ b/first_file
@@ -1 +1 @@
-first text
+changed first text

=====diff staged=====
diff --git a/second_file b/second_file
new file mode 100644
index 0000000..422845a
--- /dev/null
+++ b/second_file
@@ -0,0 +1 @@
+sefond text


## Compare two commits

You can compare two arbitrary commits using the syntax `git diff <basic commit> <comparison commit>`.

**Note** `basic commit` not necessary to be earlier that `comparison commit`.

So in the following example:

- In cycle created few commits each add some line to `file`:
    - **Note** line `val "hash$i=$(git rev-parse HEAD)"` just saves hash of last commit to variable `hash<i>`, so, for example, you can get hash of first commit from variable `$hash1`;
- `git log` just help to understand current state of the repository;
- Then I copare commits `Line 1 added` and `Line 2 added` in both options:
    - `Line 1 added` as basic commit and `Line 2 added` as comparison commit - `+Line 2`show that it was added in comparison commit relatively basic commit;
    - `Line 2 added` as basic commit and `Line 1 added` as comparison commit - `-Line 2`show that it was deleted in comparison commit relatively basic commit.

In [40]:
%%bash
mkdir diff_example
cd diff_example
git init &> /dev/null

for i in {1..3}
do
  echo "Line $i" >> file
  git add file
  git commit -m "Line $i added" &> /dev/null
  eval "hash$i=$(git rev-parse HEAD)"
done

echo "=====git log====="
git log --oneline --decorate

echo
echo "=====git diff \$hash1 \$hash2======="
git diff $hash1 $hash2
echo
echo "=====git diff \$hash2 \$hash1======="
git diff $hash2 $hash1

cd ..
rm -r diff_example

=====git log=====
c9578cb (HEAD -> master) Line 3 added
ff19e36 Line 2 added
bd6fd11 Line 1 added

=====git diff $hash1 $hash2=======
diff --git a/file b/file
index 3be9c81..c82de6a 100644
--- a/file
+++ b/file
@@ -1 +1,2 @@
 Line 1
+Line 2

=====git diff $hash2 $hash1=======
diff --git a/file b/file
index c82de6a..3be9c81 100644
--- a/file
+++ b/file
@@ -1,2 +1 @@
 Line 1
-Line 2
